# Jitter amplification in our X-band linac from 100 to 500 MeV

In [ ]:
import RF_Track
import numpy
import matplotlib.pyplot as plt

In [ ]:
def PolyArea(x,y):
    return 0.5*numpy.abs(numpy.dot(x,numpy.roll(y,1))-numpy.dot(y,numpy.roll(x,1)))

## Load the field map from a file
This field map is inspired by the structure presented in this paper: 

W. L. Millar et al., "High-Power Test of Two Prototype X-Band Accelerating Structures Based on SwissFEL Fabrication Technology," in IEEE Transactions on Nuclear Science, vol. 70, no. 1, pp. 1-19, Jan. 2023, doi: 10.1109/TNS.2022.3230567. https://ieeexplore.ieee.org/document/9991980

In [ ]:
T = numpy.loadtxt('data/TWS_Xband.dat')

## Prepare for the RF-Track element

In [ ]:
Ez = T[:,1] + 1j*T[:,2] # MV/m
hz = T[1,0] - T[0,0] # m

Let's plot it to see what it looks like

In [ ]:
plt.plot(T[:,0], Ez.real)
plt.plot(T[:,0], Ez.imag)

## Create a new element
The field map was computed assuming 37.5 MW input power to provide a 100 MV/m peak field. We want to operate this structure at an 80 MV/m peak field. In a TW structure, the power and the gradient are related by the following expression: $$G = \sqrt{\frac{\omega r/Q P}{v_g}}.$$ 

Assuming a linear relationship between the gradient $G$ and the max $E_z$ field, the required input power must be reduced according to the following expression:
$$
P_\text{actual} = P_\text{map}\left( {\frac{E_\text{z max, actual}}{E_\text{z max, map}}} \right)^2.
$$

Like in the previous example, we create a new element of type RF_FieldMap_1D, but, this time, we add two new arguments to the constructor, $ P_\text{map}$ and $P_\text{actual}$ to specify our operating input power.

In [ ]:
freq = 11.9942e9; # Hz
phid = numpy.deg2rad(0.0) # degrees

E_map = 100e6 # V/m, the max Ez
E_actual = 80e6# % V/m, our max Ez 

P_map = 37.5e6 # % W, the field map was generated assuming 37.5 MW input power, to provide 100 MV/m max Ez
P_actual = P_map * E_actual**2 / E_map**2 # W, we want to operate at 80 MV/m

RF = RF_Track.RF_FieldMap_1d(Ez, hz, -1, freq, +1, P_map, P_actual)
RF.set_phid(phid)
RF.set_nsteps(1000)

Let's plot the field using ```get_field()```

In [ ]:
RF.set_t0(0.0) # for plotting
T_period = RF.get_period() # mm/c

Z = numpy.linspace(0, RF.get_length()*1e3, 1000) # mm
O = numpy.zeros(Z.size)
I = numpy.ones(Z.size);

for t in numpy.array([0.0,0.3,0.6])*T_period:
    #read the field
    E, B  = RF.get_field(O, O, Z, t*I)
    plt.figure()
    plt.plot(Z, E[:,2] / 1e6)
    plt.title('t = {} % of period'.format(t*100/T_period))
    plt.xlabel('Z [mm]')
    plt.ylabel('E_z [MV/m]')

RF.unset_t0()

In [ ]:
L_RF = RF.get_length()

## Let's define some beam parameters

In [ ]:
# Bunch parameters
mass = RF_Track.electronmass # MeV/c^2
Q = -1 # single-particle charge, in units of e
population = 50 * RF_Track.pC # number of real particles per bunch

P_i = 100 # initial momentum, MeV/c
P_f = 500 # final momentum, MeV/c

## Let's build the linac lattice
We use a standard FODO lattice, with four structures every two consecutive quadrupoles and 90 degrees phase advance per cell

In [ ]:
# FODO cell parameters
Lquad = 0.1 # m
Lcell = 8*L_RF + 2*Lquad # m, eight structures and two quadrupoles

In [ ]:
mu = numpy.deg2rad(90) # deg
k1L = numpy.sin(mu/2) / (Lcell/4) # 1/m
k1 = k1L / Lquad # 1/m^2

### The unit FODO cell
Each FODO cell can be considered as an RF module.
Initially, we leave the quadrupoles off; their strength is 0.0.

In [ ]:
FODO = RF_Track.Lattice()
FODO.append(RF)
FODO.append(RF)
FODO.append(RF)
FODO.append(RF)
FODO.append(RF_Track.Quadrupole(Lquad, 0.0)) # initial strength to zero -> set automatically using Ref part
FODO.append(RF)
FODO.append(RF)
FODO.append(RF)
FODO.append(RF)
FODO.append(RF_Track.Quadrupole(Lquad, 0.0))

We need to find what is the maximum energy gain per cell, so we define a reference particle and track it through the cell

In [ ]:
# Define the reference particle
P0 = RF_Track.Bunch6d(mass, population, Q, numpy.array([0,0,0,0,0,P_i]).T)

# We use "autophase" to set the phases and to determine P_max, the maximum final momentum
P_max = FODO.autophase(P0) # MeV/c

# The momentum gain is
P_gain = P_max - P_i   # MeV/c

print(P_max)
print(P_gain)

Let's compute how many FODO cells we need

In [ ]:
n_FODO = (P_f - P_i) / P_gain

In [ ]:
n_FODO = int(numpy.round(n_FODO))    # let's round it to the nearest integer
print(n_FODO)

As we intend to use several instances of the same FODO cell, we need to unset the reference time from FODO so that we can put four cells in a lattice and have each have its own reference time.

In [ ]:
FODO.unset_t0()

# Start a new lattice
LINAC = RF_Track.Lattice()

# 1/2 quad, let's start with half a quad
LINAC.append(RF_Track.Quadrupole(Lquad/2, 0.0))

# let's put out n_FODO cells
for i in range(n_FODO):
    LINAC.append(FODO)

In [ ]:
LINAC.get_length()

## Let's track the reference particle and do some plots

In [ ]:
# Track the reference particle
P1 = LINAC.track(P0)

Plot the energy profile along the linac

In [ ]:
# Extract the "transport table"
T = LINAC.get_transport_table('%S %mean_P')

plt.plot (T[:, 0], T[:, 1])
plt.xlabel ('s [m]')
plt.ylabel ('K [MeV]')

Now, we need to set the quadrupole strengths. We can use ```set_K1```, which accepts two parameters:
* the reference rigidity, $P/q$
* the quadrupole's focusing strength, in 1/m$^2$

In [ ]:
Quads = LINAC.get_quadrupoles()

In [ ]:
len(Quads)

It is convenient to use the normalised focusing strength, $k_1$

In [ ]:
k1 = k1L / Lquad # 1/m^2

half_P_gain = 0.5 * P_gain

P = P_i # initial momentum
for q in Quads:
  # set quadrupole strength
  q.set_K1 (P/Q, k1)
  # update the momentum variable
  P += half_P_gain
  # changes the sign of k1, anticipating the next quadrupole
  k1 = -k1

## Define a bunch

In [ ]:
# Define Twiss parameters
Twiss = RF_Track.Bunch6d_twiss()
Twiss.emitt_x = 5 # mm.mrad, normalized emittances
Twiss.emitt_y = 5 # mm.mrad
Twiss.beta_x = Lcell * (1 - numpy.sin(mu/2)) / numpy.sin(mu) # m
Twiss.beta_y = Lcell * (1 + numpy.sin(mu/2)) / numpy.sin(mu) # m

# Create the bunch
B0 = RF_Track.Bunch6d_QR(mass, population, Q, P_i, Twiss, 10000);

Let's add an offset in X of 10% of the beam size

In [ ]:
M0 = B0.get_phase_space()

sigma_X = numpy.std(M0[:,0]) # mm

M0[:,0] += 0.1 * sigma_X # mm, add an offset in X

B0 = RF_Track.Bunch6d(mass, population, Q, M0)

## Perform tracking

In [ ]:
B1 = LINAC.track(B0)

Let's make some plots...

In [ ]:
M0 = B0.get_phase_space ('%x %xp %y %yp %dt %P')
M1 = B1.get_phase_space ('%x %xp %y %yp %dt %P')

plt.figure()
plt.plot(M0[:,0], M0[:,1], '.', label='Initial', mfc='none')
plt.plot(M1[:,0], M1[:,1], '.', label='Final', mfc='none')
plt.xlabel('x [mm]')
plt.ylabel("x' [mrad]")

plt.figure()
plt.plot(M0[:,2], M0[:,3], '.', label='Initial', mfc='none')
plt.plot(M1[:,2], M1[:,3], '.', label='Final', mfc='none')
plt.xlabel('y [mm]')
plt.ylabel("y' [mrad]")

plt.figure()
plt.plot(M1[:,4], M1[:,5], '.', label='Final', mfc='none')
plt.xlabel('t [mm/c]')
plt.ylabel('P [MeV/c]')
plt.tight_layout()

In [ ]:
T = LINAC.get_transport_table('%S %mean_x %mean_y')

In [ ]:
plt.plot(T[:,0], T[:,1], linewidth=2, label='x')
plt.plot(T[:,0], T[:,2], linewidth=2, label='y')
plt.legend()
plt.xlabel('s [m]')
plt.ylabel('position [mm]')

In [ ]:
T = LINAC.get_transport_table('%S %emitt_x %emitt_y')

In [ ]:
plt.plot(T[:,0], T[:,1], linewidth=2, label=r'$\epsilon_x$')
plt.plot(T[:,0], T[:,2], linewidth=2, label=r'$\epsilon_y$')
plt.legend()
plt.xlabel('s [m]')
plt.ylabel(r'$\epsilon_n$ [mm.mrad]')

In [ ]:
#RF = RF_Track.Drift( RF.get_length());
#RF.set_static_Efield(0, 0, -E_max);

## Jitter amplification study
We paint an ellipse in the input phase space to evaluate the action amplification (jitter amplification)

In [ ]:
N = 10
angles = numpy.linspace(0, 360, N)[:-1]

In [ ]:
M0 = B0.get_phase_space()

sigma_X  = numpy.std(M0[:,0]) # mm
sigma_Xp = numpy.std(M0[:,1]) # mrad

T_X = []
T_XP = []

for angle in angles:
    print('angle=', angle)
    Mtemp = numpy.copy(M0)
    sx = numpy.std(M0[:,0])
    sy = numpy.std(M0[:,1])
    Mtemp[:,0] += 0.1*numpy.cos(numpy.deg2rad(angle))*sx
    Mtemp[:,1] += 0.1*numpy.sin(numpy.deg2rad(angle))*sy    
    Btemp = RF_Track.Bunch6d(mass, population, Q, Mtemp)
    B1 = LINAC.track(Btemp)  
    # do plots
    T = LINAC.get_transport_table('%mean_x %mean_Px')
    T_X = numpy.concatenate((T_X, T[:, 0]))
    T_XP = numpy.concatenate((T_XP, T[:, 1]))  
    
T_X = T_X.reshape((len(angles), int(T_X.size/len(angles))))
T_XP = T_XP.reshape((len(angles), int(T_XP.size/len(angles))))

In [ ]:
T_X.size
T_X.shape

In [ ]:
plt.plot(T_X)
plt.xlabel('s [m]')
plt.ylabel('x [mm]')

In [ ]:
plt.plot(T_X[:,0], T_XP[:,0], '.')
plt.xlabel('x [mm]')
plt.ylabel(r'$p_x$ [MeV/c]')
plt.title('Offsets at linac start')

In [ ]:
plt.plot(T_X[:,-1], T_XP[:,-1], '.')
plt.xlabel('x [mm]')
plt.ylabel(r'$p_x$ [MeV/c]')
plt.title('Offsets at linac end')

In [ ]:
Ai = PolyArea(T_X[:, 0], T_XP[:, 0])

In [ ]:
Af = PolyArea(T_X[:, -1], T_XP[:, -1])

In [ ]:
Amplification_factor = Af / Ai
print(Amplification_factor)